In [1]:
# this notebook follows on from more_cleaning_normalisation

In [2]:
import numpy as np
import pandas as pd
pd.options.display.max_columns = 500
pd.options.display.max_rows = 500
from matplotlib import pyplot as plt
pd.set_option('display.max_rows', 500)

In [3]:
filename = '../Data/big_cats/processed_data/scaled_data_15_09_2021.csv'
data_scaled = pd.read_csv(filename)

# Make data trajectories of visits
For each column calculate a linear fit and use the gradient as the feature

In [5]:
data_scaled.sort_values(['ARKS Number', 'Date']).head()

ARKS Number  Acute kidney failure Age at Death  CKD - cause of mortality  \
91      200003                 False     22y0m19d                     False   
92      200003                 False     22y0m19d                     False   
93      200003                 False     22y0m19d                     False   
94      200003                 False     22y0m19d                     False   
95      200003                 False     22y0m19d                     False   

    CKD - co-morbidity Date  of Birth  Infection  Neoplasia  Neurological  \
91                True     1993-01-01      False      False         False   
92                True     1993-01-01      False      False         False   
93                True     1993-01-01      False      False         False   
94                True     1993-01-01      False      False         False   
95                True     1993-01-01      False      False         False   

    Old Age debility  Respiratory/Cardiovascular  Trauma                 Date  \
91              True                       False   False  2010-06-25 00:00:00   
92              True                       False   False  2012-07-13 00:00:00   
93              True                       False   False  2013-01-16 00:00:00   
94              True                       False   False  2014-06-20 00:00:00   
95              True                       False   False  2014-08-24 00:00:00   

    haem: RBC (x 10^12/L)  haem: haemoglobin (g/L)  haem: HCT (%)  \
91                    NaN                      NaN            NaN   
92                    NaN                      NaN            NaN   
93                    NaN                      NaN            NaN   
94                    NaN                      NaN            NaN   
95                    NaN                      NaN            NaN   

    haem: Total Protein (refractometer)  haem: leukocyte count (x10^9/L)  \
91                                  NaN                              NaN   
92                                  NaN                              NaN   
93                                  NaN                              NaN   
94                                  NaN                              NaN   
95                                  NaN                              NaN   

    haem: neutrophils (%)  haem: neutrophils (band)  \
91                    NaN                       NaN   
92                    NaN                       NaN   
93                    NaN                       NaN   
94                    NaN                       NaN   
95                    NaN                       NaN   

    haem: neutrophils(seg) (x10^9/L)  haem: lymphocytes (x10^9/L)  \
91                               NaN                          NaN   
92                               NaN                          NaN   
93                               NaN                          NaN   
94                               NaN                          NaN   
95                               NaN                          NaN   

    haem: lymphocytes  (%)  haem: monocytes (x10^9/L)  haem: monocytes (%)  \
91                     NaN                        NaN                  NaN   
92                     NaN                        NaN                  NaN   
93                     NaN                        NaN                  NaN   
94                     NaN                        NaN                  NaN   
95                     NaN                        NaN                  NaN   

    haem: eosinophils  (x10^9/L)  haem: eosinophils (%)  \
91                           NaN                    NaN   
92                           NaN                    NaN   
93                           NaN                    NaN   
94                           NaN                    NaN   
95                           NaN                    NaN   

    haem: estimated platelets x 10^9/L (Hi)  haem: MCV (fL)  haem: MCHC (g/L)  \
91                                      NaN            

In [6]:
cols_we_want = list(data_scaled.select_dtypes(include=['float', 'int']).columns)
cols_we_want.remove('num visits')
cols_we_want.remove('num key features missing')
cols_we_want.remove('Age at Death days')
cols_we_want

['haem: RBC (x 10^12/L)',
 'haem: haemoglobin (g/L)',
 'haem: HCT (%)',
 'haem: Total Protein (refractometer)',
 'haem: leukocyte count (x10^9/L)',
 'haem: neutrophils (%)',
 'haem: neutrophils (band)',
 'haem: neutrophils(seg) (x10^9/L)',
 'haem: lymphocytes (x10^9/L)',
 'haem: lymphocytes  (%)',
 'haem: monocytes (x10^9/L)',
 'haem: monocytes (%)',
 'haem: eosinophils  (x10^9/L)',
 'haem: eosinophils (%)',
 'haem: estimated platelets x 10^9/L (Hi)',
 'haem: MCV (fL)',
 'haem: MCHC (g/L)',
 'haem: MCH (pg)',
 'biochem: Low USG?',
 'biochem: BUN (mmol/L)',
 'biochem: Hypercreatininaemia?',
 'biochem: Creatinine (umol/L)',
 'biochem: Total Plasma Protein (g/L)',
 'biochem: Serum Albumin (g/L)',
 'biochem: Globulins (g/L)',
 'biochem: Anaemic? <25',
 'biochem: Haematocrit (%)',
 'biochem: Potassium (mmol/L)',
 'biochem: Calcium (mmol/L)',
 'biochem: Hyperphosphataemia? >2_9 to 3',
 'biochem: Phosphate (mmol/L)',
 'biochem: Sodium (mmol/L)',
 'biochem: Chloride (mmol/L)',
 'biochem: Bicar

In [7]:
from sklearn.linear_model import LinearRegression

feature_df = pd.DataFrame()
cats = data_scaled['ARKS Number'].unique()


for cat in cats:
    cat_data = data_scaled[data_scaled['ARKS Number'] == cat]
    gradient_dict = {}
    gradient_dict['ARKS Number'] = cat
   
    for col in cols_we_want:
        # drop nans
        cat_data_subset = cat_data.dropna(subset = [col])
        # check for 2 values
        if len(cat_data_subset) >= 2:
            # do the linear fit
            X = cat_data_subset['age at visit days'].values.reshape(-1, 1)
            y = cat_data_subset[col].values.reshape(-1, 1)
            reg = LinearRegression().fit(X, y)
            grad = reg.coef_
            intercept = reg.intercept_
            gradient_dict[col + '_grad'] = grad[0][0]
            gradient_dict[col + '_intercept'] = intercept[0]
            
        else:
            # set gradient to nan
            gradient_dict[col + '_grad'] = np.nan
            gradient_dict[col + '_intercept'] = np.nan
    
    # add this cat to the df
    feature_df = feature_df.append(gradient_dict, ignore_index = True)

In [8]:
feature_df

ARKS Number  Sex_female_grad  Sex_female_intercept  \
0       Koyukon              0.0                   0.0   
1        780127              0.0                   1.0   
2      800014MZ             -0.0                   1.0   
3        920519             -0.0                   1.0   
4        980010              0.0                   0.0   
5        980014              0.0                   1.0   
6        999028              0.0                   1.0   
7        A39042              0.0                   0.0   
8        A50003              0.0                   0.0   
9        A79192              0.0                   0.0   
10       780049              0.0                   0.0   
11       900959              0.0                   0.0   
12       930045              0.0                   1.0   
13       960093             -0.0                   0.0   
14       990948              0.0                   0.0   
15        K0095              0.0                   1.0   
16       200003              0.0                   1.0   
17       670005             -0.0                   0.0   
18       720019             -0.0                   1.0   
19       730023             -0.0                   0.0   
20       730024              0.0                   0.0   
21       750011              0.0                   1.0   
22       760022             -0.0                   1.0   
23       770005              0.0                   1.0   
24       770006             -0.0                   1.0   
25       780001              0.0                   1.0   
26       790025              0.0                   0.0   
27       790026             -0.0                   1.0   
28       790035              0.0                   1.0   
29       790036             -0.0                   0.0   
30     790036MZ              0.0                   1.0   
31       790037              0.0                   1.0   
32       790038              0.0                   1.0   
33       800015             -0.0                   0.0   
34       800017             -0.0                   1.0   
35       800029              0.0                   1.0   
36       810034              0.0                   1.0   
37       810041              0.0                   1.0   
38       810044              0.0                   1.0   
39       810053              0.0                   0.0   
40       810057              0.0                   0.0   
41       820014              0.0                   1.0   
42       820029              0.0                   1.0   
43       830014              0.0                   0.0   
44       830025             -0.0                   1.0   
45       840019              0.0                   0.0   
46       840025             -0.0                   0.0   
47       840026              0.0                   1.0   
48       840033             -0.0                   0.0   
49       840034              0.0                   1.0   
50       850007              0.0                   0.0   
51       850083              0.0                   0.0   
52       850101              0.0                   1.0   
53       860057             -0.0                   1.0   
54       860081              0.0                   0.0   
55       870008             -0.0                   0.0   
56       880014              0.0                   0.0   
57       880045             -0.0                   0.0   
58       880074              0.0                   0.0   
59       880075             -0.0                   0.0   
60       890000              0.0                   1.0   
61       890004             -0.0                   0.0   
62       890114              0.0                   0.0   
63       890254             -0.0                   0.0   
64       890290             -0.0                   1.0   
65       900248             -0.0                   0.0   
66       900249              0.0                   1.0   
67       900484             -0.0                   0.0   
68

### Make demographics df

In [9]:
dem_list = ['ARKS Number',
 'CKD - cause of mortality',
 'Species (common name)_African Lion',
 'Species (common name)_Asiatic Lion',
 'Species (common name)_Bengal Tiger',
 'Species (common name)_Bengal Tiger (white)',
 'Species (common name)_Bobcat',
 'Species (common name)_Caracal',
 'Species (common name)_Cheetah',
 'Species (common name)_Clouded Leopard',
 'Species (common name)_Cougar',
 'Species (common name)_Fishing Cat',
 'Species (common name)_Jaguar',
 'Species (common name)_Jaguarundi',
 'Species (common name)_Leopard',
 'Species (common name)_Leopard Cat',
 'Species (common name)_Lion',
 'Species (common name)_Northern (Canadian) Lynx',
 'Species (common name)_Ocelot',
 'Species (common name)_Persian Leopard',
 'Species (common name)_Serval',
 'Species (common name)_Siberian Tiger',
 'Species (common name)_Snow Leopard',
 'Species (common name)_Sumatran Tiger',
 "Species (common name)_Temminck's Golden Cat",
 'Species (common name)_Tiger',
 'Species (common name)_Tiger (White)']

In [10]:
demographics = data_scaled[dem_list].drop_duplicates()
demographics

ARKS Number  CKD - cause of mortality  \
0        Koyukon                     False   
5         780127                     False   
12      800014MZ                     False   
14        920519                     False   
20        980010                     False   
22        980014                     False   
24        999028                     False   
30        A39042                     False   
32        A50003                     False   
38        A79192                     False   
41        780049                     False   
43        900959                     False   
58        930045                     False   
67        960093                      True   
74        990948                      True   
85         K0095                     False   
91        200003                     False   
96        670005                     False   
102       720019                     False   
106       730023                      True   
110       730024                      True   
112       750011                     False   
115       760022                     False   
118       770005                      True   
120       770006                     False   
126       780001                     False   
132       790025                     False   
134       790026                      True   
138       790035                     False   
141       790036                     False   
153     790036MZ                     False   
155       790037                     False   
158       790038                      True   
169       800015                     False   
181       800017                     False   
185       800029                     False   
189       810034                     False   
195       810041                     False   
199       810044                     False   
201       810053                      True   
224       810057                     False   
226       820014                     False   
261       820029                     False   
279       830014                     False   
285       830025                     False   
288       840019                     False   
304       840025                     False   
313       840026                     False   
317       840033                      True   
321       840034                     False   
323       850007                      True   
337       850083                      True   
355       850101                     False   
358       860057                     False   
364       860081                     False   
377       870008                      True   
391       880014                      True   
401       880045                      True   
409       880074                     False   
421       880075                     False   
424       890000                      True   
440       890004                      True   
445       890114                      True   
463       890254                     False   
471       890290                     False   
497       900248                      True   
501       900249                     False   
504       900484                     False   
523       900485                     False   
538       910080                     False   
540       910517                      True   
577       920185                      True   
588       920259                     False   
592       920260                     False   
601       920453                     False   
606       920534                     False   
610       921189                     False   
627       921430                      True   
646       930228                     False   
655       930229                      True   
672       930230                     False   
674       930430                     False   
689       930431                     False   
717       940101                     False   
721       950061                      True   
756       950062                      True   
758

### Join demographcs to linear features

In [11]:
total_df = feature_df.merge(demographics, on='ARKS Number')
total_df

ARKS Number  Sex_female_grad  Sex_female_intercept  \
0       Koyukon              0.0                   0.0   
1        780127              0.0                   1.0   
2      800014MZ             -0.0                   1.0   
3        920519             -0.0                   1.0   
4        980010              0.0                   0.0   
5        980014              0.0                   1.0   
6        999028              0.0                   1.0   
7        A39042              0.0                   0.0   
8        A50003              0.0                   0.0   
9        A79192              0.0                   0.0   
10       780049              0.0                   0.0   
11       900959              0.0                   0.0   
12       930045              0.0                   1.0   
13       960093             -0.0                   0.0   
14       990948              0.0                   0.0   
15        K0095              0.0                   1.0   
16       200003              0.0                   1.0   
17       670005             -0.0                   0.0   
18       720019             -0.0                   1.0   
19       730023             -0.0                   0.0   
20       730024              0.0                   0.0   
21       750011              0.0                   1.0   
22       760022             -0.0                   1.0   
23       770005              0.0                   1.0   
24       770006             -0.0                   1.0   
25       780001              0.0                   1.0   
26       790025              0.0                   0.0   
27       790026             -0.0                   1.0   
28       790035              0.0                   1.0   
29       790036             -0.0                   0.0   
30     790036MZ              0.0                   1.0   
31       790037              0.0                   1.0   
32       790038              0.0                   1.0   
33       800015             -0.0                   0.0   
34       800017             -0.0                   1.0   
35       800029              0.0                   1.0   
36       810034              0.0                   1.0   
37       810041              0.0                   1.0   
38       810044              0.0                   1.0   
39       810053              0.0                   0.0   
40       810057              0.0                   0.0   
41       820014              0.0                   1.0   
42       820029              0.0                   1.0   
43       830014              0.0                   0.0   
44       830025             -0.0                   1.0   
45       840019              0.0                   0.0   
46       840025             -0.0                   0.0   
47       840026              0.0                   1.0   
48       840033             -0.0                   0.0   
49       840034              0.0                   1.0   
50       850007              0.0                   0.0   
51       850083              0.0                   0.0   
52       850101              0.0                   1.0   
53       860057             -0.0                   1.0   
54       860081              0.0                   0.0   
55       870008             -0.0                   0.0   
56       880014              0.0                   0.0   
57       880045             -0.0                   0.0   
58       880074              0.0                   0.0   
59       880075             -0.0                   0.0   
60       890000              0.0                   1.0   
61       890004             -0.0                   0.0   
62       890114              0.0                   0.0   
63       890254             -0.0                   0.0   
64       890290             -0.0                   1.0   
65       900248             -0.0                   0.0   
66       900249              0.0                   1.0   
67       900484             -0.0                   0.0   
68

## Write total_df to file

In [13]:
filename = '../Data/big_cats/processed_data/grad_intercept_data_15_09_2021.csv'
total_df.to_csv(filename, index=False)